In [1]:
import pandas as pd
import numpy as np
import json
import re

from rdkit import Chem
from rdkit.Chem import AllChem
from rdkit.Chem import Draw
from rdkit.Chem import PandasTools
from rdkit.Chem.Draw import IPythonConsole

from mol2vec.features import mol2alt_sentence, MolSentence, DfVec, sentences2vec
from mol2vec.helpers import depict_identifier, plot_2D_vectors, IdentifierTable, mol_to_svg

from gensim.models import word2vec

from sklearn.decomposition import PCA
from sklearn.manifold import TSNE

from pprint import pprint

from sklearn.preprocessing import StandardScaler, OneHotEncoder

import matplotlib.pyplot as plt

pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 500)

### Initialize utility files

In [2]:
with open('./rsc/fxn_grps.json', 'r') as fp:
    fxn_grp_dict = json.load(fp)
    
with open('./rsc/df_columns.json', 'r') as fp:
    column_filters = json.load(fp)
    
with open('./rsc/chems_dict.json', 'r') as fp:
    chems_dict = json.load(fp)
    
compounds = list(fxn_grp_dict.keys())

### import data files and create master dataframes

Separating into syntheses from literature and those performed in-house

In [3]:
raw_df = pd.read_csv('./data/bfo_df_20220519.csv')
raw_df = raw_df.dropna(thresh=1)

raw_lit_df = raw_df[~raw_df['doi'].isin(['Sutter-Fella Lab', 'Sutter-Fella Lab -- suggested'])]
raw_inhouse_df = raw_df[raw_df['doi'].isin(['Sutter-Fella Lab', 'Sutter-Fella Lab -- suggested'])]

print('Number of recipes from literature: ', len(raw_lit_df))
print('Number of papers: ', raw_lit_df['doi'].nunique())

print()

print('Number of in-house recipes (unprompted): ', len(raw_inhouse_df[raw_inhouse_df['doi']=='Sutter-Fella Lab']))
print('Number of in-house recipes (suggested): ', len(raw_inhouse_df[raw_inhouse_df['doi']=='Sutter-Fella Lab -- suggested']))

df = raw_df.loc[:, column_filters['master']]
#display(df)

lit_df = raw_lit_df.loc[:, column_filters['master']]
inhouse_df = raw_inhouse_df.loc[:, column_filters['master']]

df.to_csv('./data/bfo_df_master_20220519.csv')
lit_df.to_csv('./data/bfo_lit_df_master_20220519.csv')
inhouse_df.to_csv('./data/bfo_inhouse_df_master_20220519.csv')

Number of recipes from literature:  340
Number of papers:  178

Number of in-house recipes (unprompted):  17
Number of in-house recipes (suggested):  15


### Unravel specific impurity phases from `reported_impurities`

Each specific impurity needs to be converted into a column where values are one-hot encoded

In [4]:
def unravel_lists(
    series_list=[], 
    throwaway=[], # contains throwaway series and list items
    reappropriate=False, 
    one_hot_columns=[]):
    
    # if reappropriating list items, one_hot_columns must not be empty
    if reappropriate and not one_hot_columns:
        print("Please provide one_hot_columns in order to fill new dataframe")
        return
    elif reappropriate:
        unraveled_df = pd.DataFrame(np.zeros((len(series_list), len(one_hot_columns))), columns=one_hot_columns)
    elif not series_list:
        print("Please provide list_series in order to return unraveled columns for future dataframe")
    else:
        unraveled_list = []

    # cycle through series of lists and pull out individual items
    for i, row in enumerate(series_list):
        if row not in throwaway:
            contents = row[1:-1] #assuming the list items are given as a list of strings
            items = [item for item in contents.split(', ')]
            for item in items:
                item = item[1:-1]
                if item not in throwaway:
                    if not reappropriate:
                        unraveled_list.append(item)
                    else:
                        unraveled_df.at[i, item] = 1
                        
    if not reappropriate:
        return list(set(unraveled_list))
    else:
        return unraveled_df.to_numpy()
        
        
impurities = list(df['reported_impurities'])

# need to call unravel_lists twice right now (can be better constructed)
#    First to obtain the column names from unraveled lists
#    Second to obtain the one hot-encoded dataframe

impurities_list = unravel_lists(series_list=impurities, throwaway=['[]', np.nan, 'amorphous'])
impurities_array = unravel_lists(series_list=impurities, throwaway=['[]', np.nan, 'amorphous'], reappropriate=True, one_hot_columns=impurities_list)

df[impurities_list] = impurities_array

recipe_id                                                url  \
0          1.0  https://link.springer.com/content/pdf/10.1007/...   
1          2.0  https://link.springer.com/article/10.1007/s108...   
2          3.0  https://www.researchgate.net/profile/Muniyandi...   
3          4.0                                                NaN   
4          5.0                                                NaN   
5          6.0                                                NaN   
6          7.0                                                NaN   
7          8.0  https://link.springer.com/article/10.1007/s108...   
8          9.0  https://link.springer.com/article/10.1007/s108...   
9         10.0  https://link.springer.com/article/10.1007/s108...   
10        11.0                                                NaN   
11        12.0                                                NaN   
12        13.0  https://www.proquest.com/docview/1711184059/fu...   
13        14.0  https://link.springer.com/article/10.1007/s108...   
14        15.0                                                NaN   
15        16.0  https://link.springer.com/article/10.1007/s108...   
16        17.0                                                NaN   
17        18.0                                                NaN   
18        19.0                                                NaN   
19        20.0                                                NaN   
20        21.0  https://link.springer.com/article/10.1007/s108...   
21        22.0  https://link.springer.com/content/pdf/10.1007/...   
22        23.0  https://link.springer.com/article/10.1007/s108...   
23        24.0  https://link.springer.com/article/10.1007/s108...   
24        25.0  https://link.springer.com/article/10.1007/s109...   
25        26.0  https://link.springer.com/article/10.1007/s109...   
26        27.0  https://www.sciencedirect.com/science/article/...   
27        28.0  https://www.sciencedirect.com/science/article/...   
28        29.0  https://www.sciencedirect.com/science/article/...   
29        30.0  https://www.sciencedirect.com/science/article/...   
30        31.0  https://www.sciencedirect.com/science/article/...   
31        32.0  https://www.sciencedirect.com/science/article/...   
32        33.0  https://www.sciencedirect.com/science/article/...   
33        34.0  https://www.sciencedirect.com/science/article/...   
34        35.0                                                NaN   
35        36.0                                                NaN   
36        37.0                                                NaN   
37        38.0  https://www.sciencedirect.com/science/article/...   
38        39.0                                                NaN   
39        40.0                                                NaN   
40        41.0                                                NaN   
41        42.0                                                NaN   
42        43.0                                                NaN   
43        44.0                                                NaN   
44        45.0                                                NaN   
45        46.0                                                NaN   
46        47.0                                                NaN   
47        48.0                                                NaN   
48        49.0                                                NaN   
49        50.0  https://www.sciencedirect.com/science/article/...   
50        51.0  https://www.sciencedirect.com/science/article/...   
51        52.0  https://pubs.rsc.org/en/content/articlehtml/20...   
52        53.0  https://pubs.rsc.org/en/content/articlehtml/20...   
53        54.0  https://aip.scitation.org/doi/full/10.1063/1.2...   
54        55.0                                                NaN   
55        56.0                                                NaN   
56        57.0                                                NaN   
57 

### Convert specific impurity phases to binary indicator

Column indicates 1 if an impurity phase formed and 0 if synthesis was phase pure

In [5]:
#codify impurity presence
impurity_codes = df[impurities_list].sum(axis=1).astype(bool).astype(int)
df['impurity_code'] = impurity_codes

### 

### Codify type of Bi and Fe precursors

* If both Bi and Fe nitrate precursors are used, then value is 1
* If one of Bi and Fe nitrate precursor is used and other is not nitrate, value is 0
    * note that Bi is always nitrate if one of the two is nitrate
* If neither Bi nor Fe nitrate precursor is used, then value is -1

In [6]:
#codify Bi/Fe precursor
nitrate_precs = []
for i, (bi, fe) in enumerate(
    zip(df['source_Bi'].to_list(), 
        df['source_Fe'].to_list())
):
    if bi == 'bi_nitrate_pentahydrate' and fe == 'fe_nitrate_nonahydrate':
        nitrate_precs.append(1)
    elif bi == 'bi_nitrate_pentahydrate' or fe == 'fe_nitrate_nonahydrate':
        nitrate_precs.append(0) #Fe is always the other, never Bi
    else:
        nitrate_precs.append(-1)
        
df['nitrate_precs'] = nitrate_precs

### Convert `separate_hydrolysis` from boolean to 0-1 indicator

In [7]:
df['separate_hydrolysis'].fillna(False, inplace=True)
df['separate_hydrolysis'] = df['separate_hydrolysis'].astype(int)

### Treat glacial acetic acid and acetic anhydride as the same chemical

Probably shouldn't do this... but can comment out if needed

In [8]:
df.replace({'acetic_acid_glacial' : 'acetic_anhydride'}, inplace=True)
#display(df)

### One-hot encode all chemicals included in pot

* solvents
* chelating agents
* dehydrating agents

In [9]:
# Define one-hot encoder

ohe = OneHotEncoder(handle_unknown='ignore')
def get_ohes(df, column):
    ohe.fit(df[[column]])
    return pd.DataFrame(
        ohe.transform(df[[column]]).todense(),
        columns=ohe.get_feature_names([column]),
        index=df.index
    )

In [10]:
# Define solvents, dehydrating agents, and chelating agents of interest

solvents = [
    '2_methoxyethanol',
    'ethylene_glycol'
]

dehydrating_agents = [
    'acetic_acid_glacial',
    'acetic_anhydride',
    'acetylacetone'
]

chelating_agents = [
    'acetic_acid',
    'citric_acid'
]

other = [
    'trimethylene_glycol',
    'ethanol',
    'ethanolamine',
    'diethanolamine',
    'nitric_acid', 
    'ethylenediamine', 
    'ammonium_hydroxide', 
    'acetone',
    'polyvinylpyrrolidone', 
    'nn_dimethylformamide',
]

# Establish one-hot encodings for each chemical category

ohe_dfs = {
    'ohe_solvent1' : get_ohes(df, 'solvent1'),
    'ohe_solvent2' : get_ohes(df, 'solvent2'),
    'ohe_chelating_agent1' : get_ohes(df, 'chelating_agent1'),
    'ohe_chelating_agent2' : get_ohes(df, 'chelating_agent2'),
    'ohe_chelating_agent3' : get_ohes(df, 'chelating_agent3'),
    'ohe_dehydrating_agent1' : get_ohes(df, 'dehydrating_agent1'),
    'ohe_dehydrating_agent2' : get_ohes(df, 'dehydrating_agent2'),
    'ohe_surfactant' : get_ohes(df, 'surfactant') 
}
    
# Remove columns ending in "_nan"
    
for frame in ohe_dfs.keys():
    ohe_dfs[frame] = ohe_dfs[frame][ohe_dfs[frame].columns.drop(list(ohe_dfs[frame].filter(regex='_nan')))]

# Concatenate one-hot encodings to master dataframe
#     Note that this should only be run once since cell will keep concatenating one-hot encoded columns

for frame in ohe_dfs.keys():
    df = pd.concat((df, ohe_dfs[frame]), axis=1)
    
# Extract the chemicals of interest
#     Note that dehydrating agents coming before chelating agents and the order of items in the lists matters
#     at the moment since "acetic_acid" will pick up "acetic_acid_glacial". 
    
for solv in solvents:
    solv_columns = [col for col in df.columns if bool(re.match(".*_{}$".format(solv), col))]
    df[solv] = df[solv_columns].sum(axis=1)  
    df[solv].clip(upper=1.0, inplace=True)
    df = df.drop(solv_columns, axis=1)
    
for dehy in dehydrating_agents:
    dehy_columns = [col for col in df.columns if bool(re.match(".*_{}$".format(dehy), col))]
    df[dehy] = df[dehy_columns].sum(axis=1)  
    df[dehy].clip(upper=1.0, inplace=True)
    df = df.drop(dehy_columns, axis=1)
    
for chel in chelating_agents:
    chel_columns = [col for col in df.columns if bool(re.match(".*_{}$".format(chel), col))]
    df[chel] = df[chel_columns].sum(axis=1)  
    df[chel].clip(upper=1.0, inplace=True)
    df = df.drop(chel_columns, axis=1)
    
for oth in other:
    oth_columns = [col for col in df.columns if bool(re.match(".*_{}$".format(oth), col))]
    df[oth] = df[oth_columns].sum(axis=1)
    df[oth].clip(upper=1.0, inplace=True)
    df = df.drop(oth_columns, axis=1)

#display(df)

/Users/kevcruse96/anaconda3/envs/py38/lib/python3.8/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
/Users/kevcruse96/anaconda3/envs/py38/lib/python3.8/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
/Users/kevcruse96/anaconda3/envs/py38/lib/python3.8/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
/Users/kevcruse96/anaconda3/envs/py38/lib/python3.8/site-packages/skle

### Create PCA coordinates for chemicals

In [11]:
def get_values(identifier, projections, n_dim=2, c_str="chem_PCA-t-SNE-c"):
    if c_str == 'chem_PCA-t-SNE-c':
        assert n_dim < 4
    values = np.array(())
    for i in range(n_dim):
        values = np.append(values, projections[c_str + str((i+1))][str(identifier)])
    return values

In [12]:
model = word2vec.Word2Vec.load('/Users/kevcruse96/Documents/GitHub/mol2vec/examples/models/model_300dim.pkl')

mols = [Chem.MolFromSmiles(chems_dict[chem]['SMILES']) for chem in chems_dict.keys()]

mol_sentences = [mol2alt_sentence(mol, 1) for mol in mols]
flat_list = [item for sublist in mol_sentences for item in sublist]
mol_identifiers_unique = set(flat_list)

df_vec = pd.DataFrame()
df_vec['identifier'] = list(mol_identifiers_unique)
df_vec.index = df_vec['identifier']

In [13]:
pca_model = PCA(n_components=len(df_vec))
pca_result = pca_model.fit_transform([model.wv.word_vec(x) for x in mol_identifiers_unique])
tsne_model = TSNE(n_components=3, perplexity=10, n_iter=1000, metric='cosine')
tsne_pca = tsne_model.fit_transform(pca_result)

chem_pca_columns = ["chem_pca-c{}".format(i+1) for i in range(pca_result.shape[1])]
pca_df = pd.DataFrame(data=pca_result, index=list(mol_identifiers_unique), columns=chem_pca_columns)

df_vec['chem_PCA-t-SNE-c1'] = tsne_pca.T[0]
df_vec['chem_PCA-t-SNE-c2'] = tsne_pca.T[1]
df_vec['chem_PCA-t-SNE-c3'] = tsne_pca.T[2]

df_vec = df_vec.join(pca_df)
projections = df_vec.to_dict()

/Users/kevcruse96/anaconda3/envs/py38/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:780: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  warnings.warn(
/Users/kevcruse96/anaconda3/envs/py38/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:790: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  warnings.warn(
/Users/kevcruse96/anaconda3/envs/py38/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:819: FutureWarning: 'square_distances' has been introduced in 0.24 to help phase out legacy squaring behavior. The 'legacy' setting will be removed in 1.1 (renaming of 0.26), and the default setting will be changed to True. In 1.3, 'square_distances' will be removed altogether, and distances will be squared by default. Set 'square_distances'=True to silence this warning.
  warnings.warn(


In [14]:
n_dim = 30

for mol, name in zip(mols, list(chems_dict.keys())):
    pca_subs = [get_values(x, projections, n_dim=n_dim, c_str="chem_pca-c") for x in mol2alt_sentence(mol, 1)]
    summed_vec = np.array(list(sum(pca_subs)))
    chems_dict[name]['vector'] = summed_vec

Get list of constituent chemicals from each row

In [15]:
constituent_chemicals = df[list(chems_dict.keys())].apply(lambda row: row[row == 1.0].index, axis=1)

pcas = np.zeros((len(df), n_dim))

for i, rec in enumerate(constituent_chemicals):
    vectors = []
    names = rec.values
    for name in names:
        vectors.append(chems_dict[name]['vector'])
    pcas[i] = sum(vectors)

df[chem_pca_columns[:n_dim]] = pcas

### One-hot encode different annealing atmospheres

In [16]:
#codify atmosphere
air_atm = []
o2_atm = []
n2_atm = []
for atm in df['atmosphere'].tolist():
    if atm == 'O2':
        air_atm.append(0)
        o2_atm.append(1)
        n2_atm.append(0)
    elif atm == 'N2':
        air_atm.append(0)
        o2_atm.append(0)
        n2_atm.append(1)
    else:
        air_atm.append(1)
        o2_atm.append(0)
        n2_atm.append(0)
        
df['air_atm'] = air_atm
df['o2_atm'] = o2_atm
df['n2_atm'] = n2_atm

## Update qualitative values

* For now, need to simply make these NaN
* later, update them for modeling with median values

In [17]:
df['stirring_time_hr'].replace({
    "several hours" : np.nan
}, inplace=True)

df['layers'].replace({
    "several" : np.nan,
    "couple" : 2
}, inplace=True)

In [18]:
cols2del = [
    "solvent1_amount_ml",
    "solv1_solv2_ratio",
    "chelating_agent1_amount_ml",
    "chelating_agent2_amount_ml",
    "chelating_agent3_amount_ml",
    "solv_chel_ratio",
    "dehydrating_agent1_amount",
    "dehydrating_agent2_amount",
    "solv_dehydr_ratio",
    "surfactant_amount",
    "solv_surfactant_ratio",
    "solvent1_2_ethoxyethanol",
    "solvent1_ethanol",
    "solvent1_nn_dimethylformamide",
    "solvent1_propylene_glycol",
    "solvent1_trimethylene_glycol",
    "solvent1_water",
    "solvent2_ethanol",
    "solvent2_formamide",
    "solvent2_nitric_acid",
    "solvent2_polyethylene_glycol",
    "solvent2_propionic_acid",
    "chelating_agent1_ethanolamine",
    "chelating_agent1_nitric_acid",
    "chelating_agent2_diethanolamine",
    "chelating_agent2_nitric_acid",
    "chelating_agent3_ammonium_hydroxide",
    "dehydrating_agent1_acetone",
    "dehydrating_agent1_formamide",
    "dehydrating_agent1_nn_dimethylformamide",
    "dehydrating_agent2_nn_dimethylformamide",
    "surfactant_PEO-PPO-PEO",
    # delete below because we have mol2vec embeddings now
    "2_methoxyethanol",
    "ethylene_glycol",
    "acetic_acid_glacial",
    "acetic_anhydride",
    "acetylacetone",
    "acetic_acid",
    "citric_acid",
]

cols2del.extend([col for col in chem_pca_columns[n_dim:]])

for col in cols2del:
    del column_filters['modeling'][column_filters['modeling'].index(col)]

lit_df = df[~df['doi'].isin(['Sutter-Fella Lab', 'Sutter-Fella Lab -- suggested'])]
lit_df_viz = lit_df.loc[:, column_filters['modeling']]
lit_df_viz.to_csv('./data/bfo_lit_df_viz_20220524.csv')

## Update appropriate NaN values to 0

Only updating for columns which we can assume were simply not incorporated into the experiment (like aging, drying, etc.)

In [19]:
def nan2zero(df, col_regex, remove_ids=[]):
    cols = [col for col in df.columns if bool(re.match(col_regex, col))]
    if remove_ids:
        for rem in remove_ids:
            del cols[rem]
    df[cols] = df[cols].fillna(0)
    return df

### Update values in ratio columns

* If NaN but two amounts are available calculate the ratio __[TODO]__
* else, update NaN to 0

In [20]:
df = nan2zero(df, ".*_ratio$", remove_ids=[0])

### Update NaN age values to 0

In [21]:
df = nan2zero(df, "^age_")

### Update NaN low_coating values to 0

In [22]:
df = nan2zero(df, "^low_coating_.*")

### Update NaN dry values to 0

In [23]:
df = nan2zero(df, "^dry_")

### Update NaN prebake values to 0

In [24]:
df = nan2zero(df, ".*_prebake_.*")

### Update NaN layer anneal values to 0

In [25]:
df = nan2zero(df, "^layer_annealing_.*")

### Update NaN final anneal values to 0

In [26]:
df = nan2zero(df, "^final_annealing_.*")

### Save prepped dataframes to file

In [27]:
cols2del = [col for col in chem_pca_columns[n_dim:]]

for col in cols2del:
    del column_filters['eda'][column_filters['eda'].index(col)]

In [28]:
#display(df.loc[:, column_filters['eda']])

In [29]:
lit_df = df[~df['doi'].isin(['Sutter-Fella Lab', 'Sutter-Fella Lab -- suggested'])]
inhouse_df = df[df['doi'].isin(['Sutter-Fella Lab', 'Sutter-Fella Lab -- suggested'])]
only_suggested_df = df[df['doi'].isin(['Sutter-Fella Lab -- suggested'])]
suggested_df = df[~df['doi'].isin(['Sutter-Fella Lab'])]
explore_df = df[~df['doi'].isin(['Sutter-Fella Lab -- suggested'])]

df_eda = df.loc[:, column_filters['eda']]
lit_df_eda = lit_df.loc[:, column_filters['eda']]
inhouse_df_eda = inhouse_df.loc[:, column_filters['eda']]
only_suggested_df_eda = only_suggested_df.loc[:, column_filters['eda']]
suggested_df_eda = suggested_df.loc[:, column_filters['eda']]
explore_df_eda = explore_df.loc[:, column_filters['eda']]

df_eda.to_csv('./data/bfo_df_eda_20220524.csv')
lit_df_eda.to_csv('./data/bfo_lit_df_eda_20220524.csv')
inhouse_df_eda.to_csv('./data/bfo_inhouse_df_eda_20220524.csv')
only_suggested_df_eda.to_csv('./data/bfo_only_suggested_df_eda_20220524.csv')
suggested_df_eda.to_csv('./data/bfo_suggested_df_eda_20220524.csv')
explore_df_eda.to_csv('./data/bfo_explore_df_eda_20220524.csv')

### Below is for filling in blanks for layer and final prebake/annealing

This should be moved to data preprocessing for modeling, not to be used for EDA

In [30]:
#assume blank prebake times with no temp are zero
df['layer_prebake_time_min'] = df[['layer_prebake_time_min', 'layer_prebake_degC']].apply(
    lambda rec: 0 if rec['layer_prebake_degC']==0 else rec['layer_prebake_time_min'],
    axis=1
)

df['final_prebake_time_min'] = df[['final_prebake_time_min', 'final_prebake_degC']].apply(
    lambda rec: 0 if rec['final_prebake_degC']==0 else rec['final_prebake_time_min'],
    axis=1
)

df['final_prebake_time_min'] = df[['layer_prebake_time_min', 'final_prebake_time_min']].apply(
    lambda rec: rec['layer_prebake_time_min'] if rec['final_prebake_time_min']==0 else rec['final_prebake_time_min'],
    axis=1
)
df['final_prebake_degC'] = df[['layer_prebake_degC', 'final_prebake_degC']].apply(
    lambda rec: rec['layer_prebake_degC'] if rec['final_prebake_degC']==0 else rec['final_prebake_degC'],
    axis=1
)

# WARNING: NEED TO EDIT THIS (among many other things)
#     Note to self: still need to edit?
df['final_prebake_time_min'] = df['final_prebake_time_min'].fillna(df['final_prebake_time_min'].median())

#display(df['final_prebake_degC'])

In [31]:
df['final_annealing_degC'] = df['final_annealing_degC'].fillna(0)

# df['final_annealing_degC'] = df[['layer_annealing_degC', 'final_annealing_degC']].apply(
#     lambda rec: rec['layer_annealing_degC'] if rec['final_annealing_degC'] == 0 else rec['final_annealing_degC'],
#     axis=1
# )
# df['final_annealing_degC'] = df['final_annealing_degC'].fillna(0)

df['layer_annealing_degC'] = df['layer_annealing_degC'].fillna(0)
df['layer_annealing_time_min'] = df['layer_annealing_time_min'].fillna(0)

#display(df['final_annealing_degC'])

In [32]:
df['final_annealing_time_hr'] = df['final_annealing_time_hr'].fillna(0)

# df['final_annealing_time_hr'] = df[['layer_annealing_time_min', 'final_annealing_time_hr']].apply(
#     lambda rec: rec['layer_annealing_time_min'] / 60 if rec['final_annealing_time_hr'] == 0 else rec['final_annealing_time_hr'],
#     axis=1
# )
df['final_annealing_time_hr'] = df['final_annealing_time_hr'].fillna(0)

#display(df['final_annealing_time_hr'])

### Fill in NaN values for specific columns with median value from literature

Note that median values are taken from `lit_df` (might want to change that?)

In [33]:
knn_df = df.copy()
mmvi_df = df.copy()

In [34]:
mmvi_df['stirring_time_hr'] = mmvi_df['stirring_time_hr'].fillna(lit_df['stirring_time_hr'].median())
mmvi_df['stirring_temp_degC'] = mmvi_df['stirring_temp_degC'].fillna(lit_df['stirring_temp_degC'].median())

mmvi_df['high_coating_time_sec'] = mmvi_df['high_coating_time_sec'].fillna(lit_df['high_coating_time_sec'].median())
mmvi_df['high_coating_rpm'] = mmvi_df['high_coating_rpm'].fillna(lit_df['high_coating_rpm'].median())

mmvi_df['pH'] = mmvi_df['pH'].fillna(lit_df['pH'].median())

mmvi_df['bi_fe_ratio'] = mmvi_df['bi_fe_ratio'].fillna(lit_df['bi_fe_ratio'].median())

mmvi_df['precursor_concentration'] = mmvi_df['precursor_concentration'].fillna(lit_df['precursor_concentration'].median())

mmvi_df['layers'] = mmvi_df['layers'].fillna(lit_df['layers'].median())

mmvi_df['thin_film_thickness_nm'] = mmvi_df['thin_film_thickness_nm'].fillna(lit_df['thin_film_thickness_nm'].median())

### Update values of amounts/ratios/etc.

__TODO__: fill this in

In [35]:
# For now, just ignore amount and ratio columns

cols2del = [
    "solvent1_amount_ml",
    "solv1_solv2_ratio",
    "chelating_agent1_amount_ml",
    "chelating_agent2_amount_ml",
    "chelating_agent3_amount_ml",
    "solv_chel_ratio",
    "dehydrating_agent1_amount",
    "dehydrating_agent2_amount",
    "solv_dehydr_ratio",
    "surfactant_amount",
    "solv_surfactant_ratio",
    "solvent1_2_ethoxyethanol",
    "solvent1_ethanol",
    "solvent1_nn_dimethylformamide",
    "solvent1_propylene_glycol",
    "solvent1_trimethylene_glycol",
    "solvent1_water",
    "solvent2_ethanol",
    "solvent2_formamide",
    "solvent2_nitric_acid",
    "solvent2_polyethylene_glycol",
    "solvent2_propionic_acid",
    "chelating_agent1_ethanolamine",
    "chelating_agent1_nitric_acid",
    "chelating_agent2_diethanolamine",
    "chelating_agent2_nitric_acid",
    "chelating_agent3_ammonium_hydroxide",
    "dehydrating_agent1_acetone",
    "dehydrating_agent1_formamide",
    "dehydrating_agent1_nn_dimethylformamide",
    "dehydrating_agent2_nn_dimethylformamide",
    "surfactant_PEO-PPO-PEO",
    # delete below because we have mol2vec embeddings now
    "2_methoxyethanol",
    "ethylene_glycol",
    "acetic_acid_glacial",
    "acetic_anhydride",
    "acetylacetone",
    "acetic_acid",
    "citric_acid",
]

cols2del.extend([col for col in chem_pca_columns[n_dim:]])

for col in cols2del:
    if col in column_filters['modeling']:
        del column_filters['modeling'][column_filters['modeling'].index(col)]

### Implement KNN imputation

In [50]:
from sklearn.impute import KNNImputer

display(knn_df)

knn_df = knn_df.loc[:, column_filters['modeling']]

np_data = knn_df.to_numpy()
imputer = KNNImputer(n_neighbors=5, weights='distance')
imputed_df = pd.DataFrame(imputer.fit_transform(np_data))
imputed_df.columns = knn_df.columns
display(imputed_df)

recipe_id  bi_fe_ratio  separate_hydrolysis  precursor_concentration  \
0          1.0        1.100                    0                    0.200   
1          2.0        1.050                    0                    0.200   
2          3.0        1.100                    0                      NaN   
3          4.0        1.100                    0                      NaN   
4          5.0        1.100                    0                      NaN   
5          6.0        1.100                    0                      NaN   
6          7.0        1.100                    0                      NaN   
7          8.0        1.050                    0                    0.300   
8          9.0        1.100                    0                      NaN   
9         10.0        1.100                    0                    0.200   
10        11.0        1.100                    0                    0.200   
11        12.0        1.100                    0                    0.200   
12        13.0        1.050                    0                    0.300   
13        14.0        1.100                    0                    0.300   
14        15.0        1.100                    0                    0.300   
15        16.0        1.000                    0                    0.300   
16        17.0        1.050                    0                    0.300   
17        18.0        1.100                    0                    0.300   
18        19.0        1.150                    0                    0.300   
19        20.0        1.300                    0                    0.300   
20        21.0          NaN                    0                      NaN   
21        22.0          NaN                    0                      NaN   
22        23.0        1.000                    0                      NaN   
23        24.0        1.050                    0                    0.300   
24        25.0        1.050                    0                    0.300   
25        26.0          NaN                    0                      NaN   
26        27.0        1.050                    0                    0.200   
27        28.0        1.050                    0                    0.300   
28        29.0        1.050                    0                    0.300   
29        30.0        1.100                    0                    0.300   
30        31.0        1.100                    0                      NaN   
31        32.0          NaN                    0                      NaN   
32        33.0        1.090                    0                      NaN   
33        34.0        1.000                    0                      NaN   
34        35.0        1.000                    0                      NaN   
35        36.0        1.000                    0                      NaN   
36        37.0        1.000                    0                      NaN   
37        38.0        1.000                    0                    0.200   
38        39.0        1.050                    0                    0.200   
39        40.0        1.100                    0                    0.200   
40        41.0        1.150                    0                    0.200   
41        42.0        1.000                    0                    0.200   
42        43.0        1.050                    0                    0.200   
43        44.0        1.100                    0                    0.200   
44        45.0        1.150                    0                    0.200   
45        46.0        1.000                    0                    0.200   
46        47.0        1.050                    0                    0.200   
47        48.0        1.100                    0                    0.200   
48        49.0        1.150                    0                    0.200   
49        50.0        1.050                    0                    0.300   
50        51.0        1.100                    0                      NaN   
5

recipe_id  bi_fe_ratio  separate_hydrolysis  precursor_concentration  \
0          1.0     1.100000                  0.0                 0.200000   
1          2.0     1.050000                  0.0                 0.200000   
2          3.0     1.100000                  0.0                 0.204880   
3          4.0     1.100000                  0.0                 0.273737   
4          5.0     1.100000                  0.0                 0.236616   
5          6.0     1.100000                  0.0                 0.236705   
6          7.0     1.100000                  0.0                 0.236802   
7          8.0     1.050000                  0.0                 0.300000   
8          9.0     1.100000                  0.0                 0.236973   
9         10.0     1.100000                  0.0                 0.200000   
10        11.0     1.100000                  0.0                 0.200000   
11        12.0     1.100000                  0.0                 0.200000   
12        13.0     1.050000                  0.0                 0.300000   
13        14.0     1.100000                  0.0                 0.300000   
14        15.0     1.100000                  0.0                 0.300000   
15        16.0     1.000000                  0.0                 0.300000   
16        17.0     1.050000                  0.0                 0.300000   
17        18.0     1.100000                  0.0                 0.300000   
18        19.0     1.150000                  0.0                 0.300000   
19        20.0     1.300000                  0.0                 0.300000   
20        21.0     1.070000                  0.0                 0.250000   
21        22.0     1.062080                  0.0                 0.250000   
22        23.0     1.000000                  0.0                 0.213351   
23        24.0     1.050000                  0.0                 0.300000   
24        25.0     1.050000                  0.0                 0.300000   
25        26.0     1.074674                  0.0                 0.245165   
26        27.0     1.050000                  0.0                 0.200000   
27        28.0     1.050000                  0.0                 0.300000   
28        29.0     1.050000                  0.0                 0.300000   
29        30.0     1.100000                  0.0                 0.300000   
30        31.0     1.100000                  0.0                 0.219740   
31        32.0     1.025593                  0.0                 0.211964   
32        33.0     1.090000                  0.0                 0.209994   
33        34.0     1.000000                  0.0                 0.257807   
34        35.0     1.000000                  0.0                 0.255821   
35        36.0     1.000000                  0.0                 0.256176   
36        37.0     1.000000                  0.0                 0.257941   
37        38.0     1.000000                  0.0                 0.200000   
38        39.0     1.050000                  0.0                 0.200000   
39        40.0     1.100000                  0.0                 0.200000   
40        41.0     1.150000                  0.0                 0.200000   
41        42.0     1.000000                  0.0                 0.200000   
42        43.0     1.050000                  0.0                 0.200000   
43        44.0     1.100000                  0.0                 0.200000   
44        45.0     1.150000                  0.0                 0.200000   
45        46.0     1.000000                  0.0                 0.200000   
46        47.0     1.050000                  0.0                 0.200000   
47        48.0     1.100000                  0.0                 0.200000   
48        49.0     1.150000                  0.0                 0.200000   
49        50.0     1.050000                  0.0                 0.300000   
50        51.0     1.100000                  0.0                 0.259062   
5

In [51]:
mmvi_lit_df = mmvi_df[~df['doi'].isin(['Sutter-Fella Lab', 'Sutter-Fella Lab -- suggested'])]
mmvi_inhouse_df = mmvi_df[df['doi'].isin(['Sutter-Fella Lab', 'Sutter-Fella Lab -- suggested'])]
mmvi_only_suggested_df = mmvi_df[df['doi'].isin(['Sutter-Fella Lab -- suggested'])]
mmvi_suggested_df = mmvi_df[~df['doi'].isin(['Sutter-Fella Lab'])]

mmvi_df_modeling = mmvi_df.loc[:, column_filters['modeling']]
mmvi_lit_df_modeling = mmvi_lit_df.loc[:, column_filters['modeling']]
mmvi_inhouse_df_modeling = mmvi_inhouse_df.loc[:, column_filters['modeling']]
mmvi_only_suggested_df_modeling = mmvi_only_suggested_df.loc[:, column_filters['modeling']]
mmvi_suggested_df_modeling = mmvi_suggested_df.loc[:, column_filters['modeling']]
explore_df_modeling = explore_df.loc[:, column_filters['modeling']]

mmvi_df_modeling.to_csv('./data/bfo_df_modeling_mmvi_20220825.csv')
mmvi_lit_df_modeling.to_csv('./data/bfo_lit_df_modeling_mmvi_20220825.csv')
mmvi_inhouse_df_modeling.to_csv('./data/bfo_inhouse_df_modeling_mmvi_20220825.csv')
mmvi_only_suggested_df_modeling.to_csv('./data/bfo_only_suggested_df_modeling_mmvi_20220825.csv')
mmvi_suggested_df_modeling.to_csv('./data/bfo_suggested_df_modeling_mmvi_20220825.csv')
#explore_df_modeling.to_csv('./data/bfo_explore_df_modeling_20220825.csv')

In [52]:
knn_lit_df = knn_df[~df['doi'].isin(['Sutter-Fella Lab', 'Sutter-Fella Lab -- suggested'])]
knn_inhouse_df = knn_df[df['doi'].isin(['Sutter-Fella Lab', 'Sutter-Fella Lab -- suggested'])]
knn_only_suggested_df = knn_df[df['doi'].isin(['Sutter-Fella Lab -- suggested'])]
knn_suggested_df = knn_df[~df['doi'].isin(['Sutter-Fella Lab'])]

knn_df_modeling = knn_df.loc[:, column_filters['modeling']]
knn_lit_df_modeling = knn_lit_df.loc[:, column_filters['modeling']]
knn_inhouse_df_modeling = knn_inhouse_df.loc[:, column_filters['modeling']]
knn_only_suggested_df_modeling = knn_only_suggested_df.loc[:, column_filters['modeling']]
knn_suggested_df_modeling = knn_suggested_df.loc[:, column_filters['modeling']]
explore_df_modeling = explore_df.loc[:, column_filters['modeling']]

knn_df_modeling.to_csv('./data/bfo_df_modeling_knn_20220825.csv')
knn_lit_df_modeling.to_csv('./data/bfo_lit_df_modeling_knn_20220825.csv')
knn_inhouse_df_modeling.to_csv('./data/bfo_inhouse_df_modeling_knn_20220825.csv')
knn_only_suggested_df_modeling.to_csv('./data/bfo_only_suggested_df_modeling_knn_20220825.csv')
knn_suggested_df_modeling.to_csv('./data/bfo_suggested_df_modeling_knn_20220825.csv')
#explore_df_modeling.to_csv('./data/bfo_explore_df_modeling_20220825.csv')

In [ ]:
plt.plot(df['chem_pca-c3'])